In [ ]:
! pip install transformers datasets evaluate

In [ ]:
! pip install transformers[sentencepiece]

In [ ]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("openai-gpt")
if tokenizer.pad_token is None:
    tokenizer.add_special_tokens({'pad_token': '[PAD]'})

Using pad_token, but it is not set yet.


In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split

data = pd.read_csv("ielts_writing_dataset_new.csv")

data.label = data.label.replace(1,0)
data.label = data.label.replace(3,0)
data.label = data.label.replace(3.5,0)
data.label = data.label.replace(4,0)
data.label = data.label.replace(4.5,0)
data.label = data.label.replace(5,0)
data.label = data.label.replace(5.5,1)
data.label = data.label.replace(6,1)
data.label = data.label.replace(6.5,1)
data.label = data.label.replace(7,1)
data.label = data.label.replace(7.5,1)
data.label = data.label.replace(8,2)
data.label = data.label.replace(8.5,2)
data.label = data.label.replace(9,2)

data.label = data.label.astype(int)

train, test = train_test_split(data, test_size=0.2)


In [ ]:
data[:10]

label                                               text
0      1  Between 1995 and 2010, a study was conducted r...
1      1  Poverty represents a worldwide crisis. It is t...
2      0  The left chart shows the population change hap...
3      1  Human beings are facing many challenges nowada...
4      1  Information about the thousands of visits from...
5      1  Whether countries should only invest facilitie...
6      1  This graph depicts the changes in tourists vis...
7      1  Sports is an essential part to most of us , so...
8      2  The line graph illustrates the number of overs...
9      2  International sports events require the most w...

In [ ]:
import datasets
from datasets import Dataset, DatasetDict

train = Dataset.from_pandas(train)
test = Dataset.from_pandas(test)


dataset = DatasetDict()

dataset['train'] = train
dataset['test'] = test
dataset = dataset.remove_columns(["__index_level_0__"])
dataset

DatasetDict({
    train: Dataset({
        features: ['label', 'text'],
        num_rows: 1148
    })
    test: Dataset({
        features: ['label', 'text'],
        num_rows: 287
    })
})

In [ ]:
dataset["test"][0]

{'label': 1,
 'text': 'Information about the thousands of visits from overseas to three different European natural places during 1987 and 2007 is provided in the given line chart.\nOverall, it can be seen that the number of visitors increased significantly in the three places compared to the initial year. Although, visits to Europeans lakes demostrated more changes over the 20 years than its counterparts.\nIn more detail, the most steady growth was experienced by the visits to Europeans mountains. For example, from 1987 the number of visitors grew from 20,000 to almost the double 20 years later. Similarly, visits to the coast also rose after a slight fall in 1992, reaching almost twice as much since 1987, with 75,000.\nThose visiting Europeans lakes subtantially increased over the years from 10 thousand to a peak of 75 thousand in 2002. Despite falling for about 25 thousand in 2007, the visitis to this place remained higher compared to 1987, with 50,000 at the end of the period.'}

In [ ]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [ ]:
tokenized_dataset = dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/1148 [00:00<?, ? examples/s]

Map:   0%|          | 0/287 [00:00<?, ? examples/s]

In [ ]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

In [ ]:
tokenized_dataset['train']

Dataset({
    features: ['label', 'text', 'input_ids', 'attention_mask'],
    num_rows: 1148
})

In [ ]:
import evaluate

accuracy = evaluate.load("accuracy")

In [ ]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

In [ ]:
# id2label = {0: '1', 1:'3', 2:'3.5', 3:'4', 4:'4.5',5:'5', 6:'5.5', 7:'6', 8:'6.5',9:'7',10:'7.5',11:'8',12:'8.5',13:'9'}
# label2id = {'1':0,'3':1,'3.5':2,'4':3,'4.5':4,'5':5,'5.5':6,'6':7,'6.5':8,'7':9,'7.5':10,'8':11,'8.5':12,'9':13}
id2label = {0:"Bad",1:"Acceptable",2:"Excellent"}
label2id = {"Bad":0,"Acceptable":1,"Excellent":2}



In [ ]:
# ! pip install -q -U bitsandbytes
# ! pip install -q -U git+https://github.com/huggingface/transformers.git
# ! pip install -q -U git+https://github.com/huggingface/peft.git
# ! pip install -q -U git+https://github.com/huggingface/accelerate.git


In [ ]:
!python -m pip install huggingface_hub
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|
    
    A token is already saved on your machine. Run `huggingface-cli whoami` to get more information or `huggingface-cli logout` if you want to log out.
    Setting a new token will erase the existing one.
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) Y
Token is valid (permission: write).
Cannot authenticate through git-c

In [ ]:
from transformers import OpenAIGPTForSequenceClassification, TrainingArguments, Trainer

model = OpenAIGPTForSequenceClassification.from_pretrained("openai-gpt",num_labels=3, id2label=id2label, label2id=label2id)


Some weights of OpenAIGPTForSequenceClassification were not initialized from the model checkpoint at openai-gpt and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
! pip install transformers[torch]

In [ ]:
# from torch import nn

# class ClassificationTrainer(Trainer):
#     def compute_loss(self, model, inputs, return_outputs=False):
#         labels = inputs.get("label")
#         outputs = model(**inputs)
#         outputs = outputs.unsqueeze(1)
#         logits = outputs.get('logits')
#         loss_fct = nn.CrossEntropyLoss()
#         loss = loss_fct(logits.squeeze(), labels.squeeze())
#         return (loss, outputs) if return_outputs else loss

In [ ]:
training_args = TrainingArguments(
    output_dir="essayl0",
    learning_rate=2e-5,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=1,
    num_train_epochs=15,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    push_to_hub = True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["test"],
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

/content/essayl0 is already a clone of https://huggingface.co/karanzrk/essayl0. Make sure you pull the latest changes with `repo.git_pull()`.
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a OpenAIGPTTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=17220, training_loss=0.23190565678960665, metrics={'train_runtime': 2746.6484, 'train_samples_per_second': 6.269, 'train_steps_per_second': 6.269, 'total_flos': 2652418758988800.0, 'train_loss': 0.23190565678960665, 'epoch': 15.0})

In [ ]:
# !zip -r /content/checkpoint.zip /content/essayl0/checkpoint-1080/